In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import re


# Prepare data

## Load dataset

In [2]:
import csv
import os
import sys
import codecs
from glob import glob
from xml.dom.minidom import parse, parseString
from nltk import WordPunctTokenizer

print("entered xmlparser.py")

# Parcourir tout sous-dossiers et avoir les fichiers dans ces sous-dossiers.
def get_file_names(dirname):
    files = []
    os.chdir(dirname)
    start_dir = os.getcwd()
    pattern = "*.xml"
    for dir,_,_ in os.walk(start_dir):
        files = files + glob(os.path.join(dir, pattern))

    non_empty_files = []
    for fname in files:
        with codecs.open(fname, "r", encoding="utf-8") as f:
            ct = f.read()
            if len(ct) > 0:
                non_empty_files.append(fname)

    print("obtained " + str(len(non_empty_files)) + " files from " + start_dir) 
    print("returning to initial directory...")
    os.chdir(start_dir)
    os.chdir("..")
    print("current directory: " + os.getcwd())
    return non_empty_files



entered xmlparser.py


In [3]:
import csv
# un fichier = une jurisprudence
# Extraire les informations de chaque fichier(de chaque jurisprudence)
def parse_french_data(non_empty_files):
    count = 0
    L=[['idx', 'formation','solution','date','content','articles','citation']]
    for fname in non_empty_files:
    #for fname in glob("*.xml"):
        try:
            dom=parse(fname)
            for node in dom.getElementsByTagName('ID'):
                idx = node.toxml()
            for node in dom.getElementsByTagName('BLOC_TEXTUEL'):
                contenu = node.toxml()
            for node in dom.getElementsByTagName('FORMATION'):
                formation = node.toxml()
            for node in dom.getElementsByTagName('DATE_DEC'):
                date = node.toxml()
            for node in dom.getElementsByTagName('DATE_DEC_ATT'):
                date_att = node.toxml()
            for node in dom.getElementsByTagName('SOLUTION'):
                solution=node.toxml()
            for node in dom.getElementsByTagName('LIEN'):
                citation = node.toxml()

            if ("<CONTENU/>" in contenu) and ("<CONTENU>" not in contenu):
                contenu = ""
            else:
                contenu=contenu.replace("<BLOC_TEXTUEL>","")
                contenu=contenu.replace("<CONTENU>", "")
                contenu=contenu.replace("</BLOC_TEXTUEL>","")
                contenu=contenu.replace("</CONTENU>", "")
                contenu=contenu.replace("<br/>","")
                contenu=contenu.replace("<p>","")
                contenu=contenu.replace("</p>","")
                contenu=contenu.replace("\n"," ")
                contenu=contenu.replace("\t"," ")


            if contenu == "":
                for node in dom.getElementsByTagName('SOMAIRE'):
                    contenu = node.toxml()

            content = WordPunctTokenizer().tokenize(contenu)
            articles = []
            
            for i in range(len(content)-2):
                if content[i].lower() == "par" and content[i+1].lower() == "ces" and content[i+2].lower() == "motifs" :
                    content=content[0:i]

            
                    
            

            for i in range(len(content)):
                if (content[i].lower() == "article") or (content[i] == "Article"):
                    articles.append(content[i+1])


            articles = " ".join(articles)
            content = ' '.join(content) # joins the elements of the list content

            idx = idx.replace("<ID>", "")
            idx = idx.replace("</ID>", "")

            if "<FORMATION/>" == formation:
                formation =""
            else:
                formation = formation.replace("<FORMATION>","")
                formation = formation.replace("</FORMATION>","")
                formation = formation.replace("\t"," ")
                formation = formation.replace("\n"," ")

            if "<DATE_DEC/>" == date:
                date =""
            else:
                date = date.replace("<DATE_DEC>","")
                date = date.replace("</DATE_DEC>","")
                date = date.replace("\t"," ")
                date = date.replace("\n"," ")

            if "<DATE_DEC_ATT/>" == date_att:
                date_att = ""
            else:
                date_att = date_att.replace("<DATE_DEC_ATT>","")
                date_att = date_att.replace("</DATE_DEC_ATT>","")
                date_att = date_att.replace("\t"," ")
                date_att = date_att.replace("\n"," ")

            if solution == "<SOLUTION/>": # if solution field is empty
                solution = "" # replace field with "" to simplify
            else: # else clean up
                solution = solution.replace("<SOLUTION>","")
                solution = solution.replace("</SOLUTION>","")
                solution = solution.replace(".","")
                solution = solution.replace("non lieu","non-lieu")
                solution = solution.replace("\t"," ")
                solution = solution.replace("\n"," ")

            if re.search(">.+<", citation) == None:
                citation = ""
            else:
                citation = (re.search(">.+<", citation)).group()
                citation = citation[1:len(citation)-1]
                citation = citation.replace("\t", " ")
                citation = citation.replace("\n", " ")

            if "2999" in date_att:
                csv = idx + "\t"+formation+"\t"+solution+"\t"+date+"\t"+content+"\t"+articles+"\t"+citation+"\n"
            else:
                csv = idx + "\t"+formation+"\t"+solution+"\t"+date_att+"\t"+content+"\t"+articles+"\t"+citation+"\n"
            
            count = count + 1
            # L[count][0]=idx
            # L[count][1]=formation
            # L[count][2]=
            # L[count][3]=
            # L[count][4]=
            # L[count][5]=
            L=L+[[str(idx), str(formation) , str(solution), str(date), str(content) , str(articles) , str(citation)]]        
        except Exception as er:
            print(er)

    
    return L

In [4]:
import csv
path = '/home/nono/Documents/Legal/Data/Freemium_cass_global_20220417-170000'  # DOSSIER qui contient l'ensemble des fichiers XML
type(get_file_names(path))
files=get_file_names(path)
files[15]
M=parse_french_data(files)
len(M)
Headers=M.pop(0)
df = pd.DataFrame(M, columns=Headers)
df


obtained 140335 files from /home/nono/Documents/Legal/Data/Freemium_cass_global_20220417-170000
returning to initial directory...
current directory: /home/nono/Documents/Legal/Data
obtained 140335 files from /home/nono/Documents/Legal/Data/Freemium_cass_global_20220417-170000
returning to initial directory...
current directory: /home/nono/Documents/Legal/Data
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out of range
list index out

idx            formation  \
0      JURITEXT000006985777  CHAMBRE_COMMERCIALE   
1      JURITEXT000006981594  CHAMBRE_COMMERCIALE   
2      JURITEXT000006985050  CHAMBRE_COMMERCIALE   
3      JURITEXT000006983862  CHAMBRE_COMMERCIALE   
4      JURITEXT000006982696  CHAMBRE_COMMERCIALE   
...                     ...                  ...   
15279  JURITEXT000007020819      CHAMBRE_SOCIALE   
15280  JURITEXT000043168245      CHAMBRE_SOCIALE   
15281  JURITEXT000045167514      CHAMBRE_SOCIALE   
15282  JURITEXT000036803197      CHAMBRE_SOCIALE   
15283  JURITEXT000039188484      CHAMBRE_SOCIALE   

                            solution        date  \
0                              REJET  1971-07-12   
1                              REJET  1969-12-08   
2                          Cassation  1971-03-17   
3                    REJET Cassation  1971-01-13   
4                              REJET  1970-02-04   
...                              ...         ...   
15279                         Rejet   1988-05-11   
15280               Avis sur saisine  2021-02-11   
15281  Rejet non spécialement motivé  2022-02-09   
15282               Avis sur saisine  2018-04-04   
15283                Non-lieu a avis  2019-09-25   

                                                 content  \
0      SUR LE PREMIER MOYEN , PRIS EN SES DEUX BRANCH...   
1      SUR LE MOYEN UNIQUE : ATTENDU QU ' IL RESULTE ...   
2      SUR LE MOYEN UNIQUE , PRIS EN SES DEUX BRANCHE...   
3      SUR LE PREMIER MOYEN , PRIS EN SES DEUX BRANCH...   
4      SUR LE PREMIER MOYEN : ATTENDU QU ' IL RESULTE...   
...                                                  ...   
15279  Sur le moyen unique du pourvoi principal , pri...   
15280  LA COUR DE CASSATION , CHAMBRE SOCIALE , a ren...   
15281  LA COUR DE CASSATION , CHAMBRE SOCIALE , a ren...   
15282  LA COUR DE CASSATION , CHAMBRE SOCIALE , a ren...   
15283  LA COUR DE CASSATION , CHAMBRE SOCIALE , a ren...   

                                     articles  \
0                                               
1                                               
2                                        1134   
3                                     DE 5045   
4                                               
...                                       ...   
15279                     14 , 13 12 13 13 ne   
15280                       L L L L L L L L R   
15281  1014 700 L L L 624 L L 1315 1353 L 624   
15282                          10 L 10 . 10 R   
15283                               24 24 L R   

                                                citation  
0                                        Code civil 1650  
1                                   Code de commerce 179  
2                                        Code civil 1134  
3                     Décret 63-254 1963-03-14 ART. 5045  
4                           Code de procédure civile 168  
...                                                  ...  
15279  Convention collective nationale des transports...  
15280        article L. 1254-21, II, du code du travail.  
15281             Article R. 2314-24 du code du travail.  
15282                   principe d'égalité de traitement  
15283          article L. 1111-2, 3°, du code du travail  

[15284 rows x 7 columns]

In [5]:
df.to_csv(r'/home/nono/Documents/Legal/Data/Jurisprudences_cass_1.0.csv', index = False)


In [6]:
len(df['content'][100])



0

In [7]:
from transformers import CamembertTokenizer, CamembertModel
model_name = "camembert-base"
tokenizer = CamembertTokenizer.from_pretrained("camembert-base")
model = CamembertModel.from_pretrained('camembert-base')

In [8]:
# convert les phrases en miniscule et tokenisation avec Camemebert tokenizer
corpus_tokens_ = [tokenizer.tokenize(doc.lower()) for doc in df.content]
assert(len(corpus_tokens_)==len(df))
corpus_tokens_[0] #la première phrase tokenized
df['tokenized_sent'] = corpus_tokens_
df.head()
df.tokenized_sent[0]

['▁sur',
 '▁le',
 '▁premier',
 '▁moyen',
 '▁',
 ',',
 '▁pris',
 '▁en',
 '▁ses',
 '▁deux',
 '▁branches',
 '▁:',
 '▁attendu',
 '▁qu',
 '▁',
 "'",
 '▁il',
 '▁est',
 '▁reproche',
 '▁a',
 '▁l',
 '▁',
 "'",
 '▁arret',
 '▁de',
 'fer',
 'e',
 '▁(',
 '▁rennes',
 '▁',
 ',',
 '▁4',
 '▁fe',
 'vrier',
 '▁1970',
 '▁)',
 '▁d',
 '▁',
 "'",
 '▁avoir',
 '▁debout',
 'e',
 '▁la',
 '▁societe',
 '▁d',
 'if',
 '▁-',
 '▁',
 'kal',
 'onde',
 'ro',
 '▁de',
 '▁sa',
 '▁demande',
 '▁en',
 '▁paye',
 'ment',
 '▁de',
 '▁la',
 '▁somme',
 '▁de',
 '▁3',
 '▁',
 '.',
 '▁600',
 '▁francs',
 '▁',
 ',',
 '▁prix',
 '▁d',
 '▁',
 "'",
 '▁un',
 '▁mobilier',
 '▁qu',
 '▁',
 "'",
 '▁elle',
 '▁pret',
 'end',
 'ait',
 '▁avoir',
 '▁vendu',
 '▁a',
 '▁d',
 'an',
 'iel',
 '▁et',
 '▁de',
 '▁ses',
 '▁demandes',
 '▁accessoires',
 '▁',
 ',',
 '▁alors',
 '▁d',
 '▁',
 "'",
 '▁une',
 '▁part',
 '▁',
 ',',
 '▁que',
 '▁la',
 '▁vente',
 '▁et',
 'ait',
 '▁parfaite',
 '▁des',
 '▁le',
 '▁2',
 '▁mai',
 '▁1968',
 '▁',
 ',',
 '▁date',
 '▁de',
 '▁la',
 '▁s

In [9]:
tokenizer.encode(df.tokenized_sent[0]) 

Token indices sequence length is longer than the specified maximum sequence length for this model (922 > 512). Running this sequence through the model will result in indexing errors


[5,
 32,
 16,
 246,
 694,
 21,
 7,
 523,
 22,
 89,
 116,
 7983,
 43,
 4903,
 46,
 21,
 11,
 51,
 30,
 9550,
 33,
 17,
 21,
 11,
 16135,
 8,
 3747,
 35,
 38,
 18441,
 21,
 7,
 181,
 4152,
 16441,
 7254,
 936,
 18,
 21,
 11,
 190,
 7093,
 35,
 13,
 30259,
 18,
 1239,
 67,
 21,
 25520,
 5008,
 1259,
 8,
 77,
 400,
 22,
 9480,
 131,
 8,
 13,
 2124,
 8,
 135,
 21,
 9,
 4456,
 7137,
 21,
 7,
 258,
 18,
 21,
 11,
 23,
 4798,
 46,
 21,
 11,
 109,
 16440,
 904,
 199,
 190,
 5004,
 33,
 18,
 364,
 4177,
 14,
 8,
 89,
 3083,
 2532,
 21,
 7,
 183,
 18,
 21,
 11,
 28,
 292,
 21,
 7,
 27,
 13,
 702,
 14,
 199,
 2326,
 20,
 16,
 118,
 667,
 12314,
 21,
 7,
 749,
 8,
 13,
 4186,
 25,
 212,
 8,
 1063,
 13540,
 17,
 21,
 11,
 1909,
 20,
 1503,
 32,
 13,
 337,
 14,
 32,
 16,
 258,
 21,
 7,
 16,
 82,
 27,
 19,
 21,
 31118,
 6718,
 25,
 9480,
 131,
 7433,
 3636,
 16135,
 35,
 80,
 178,
 13,
 1769,
 23664,
 35,
 24,
 8,
 7955,
 8,
 27144,
 49,
 21,
 11,
 634,
 456,
 5262,
 28,
 1853,
 8,
 13,
 513,
 25,
 12